In [1]:
from TraceLens import TreePerfAnalyzer
from TraceLens.util import DataLoader
from TraceLens.Trace2Tree.trace_to_tree import JaxTraceToTree
from TraceLens.util import TraceEventUtils

In [2]:

# profile_filepath = "/workspace/code/traces/logs/20250509_1604_mixtral/tw026/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/tw026.xplane.pb"
profile_filepath = "/workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/tw034.xplane.pb"

In [3]:
data_pb = DataLoader.load_data(profile_filepath, save_preprocessed=False)
data_pb = data_pb['traceEvents']
jax = True
linking_key = 'correlation_id'
categorizer =  JaxTraceToTree.default_categorizer if not jax else TraceEventUtils.prepare_event_categorizer(data_pb)
data = data_pb if not jax else TraceEventUtils.non_metadata_events(data_pb)
tree = JaxTraceToTree(data, event_to_category=categorizer, linking_key=linking_key)


Received old tool format: trace_viewer@^; mapped to new format: trace_viewer@
I0000 00:00:1758874309.303071  944026 xplane_to_tools_data.cc:388] serving tool: trace_viewer@ with options: {}
I0000 00:00:1758874311.802590  944026 xprof_thread_pool_executor.cc:22] Creating derived_timeline_trace_events XprofThreadPoolExecutor with 8 threads.
I0000 00:00:1758874321.453852  944026 trace_events.cc:275] Storing 7298524 as LevelDb table fast file: /workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/tw034.SSTABLE with 0 events dropped.
I0000 00:00:1758874323.505314  944026 trace_events.cc:389] Loaded 7298524 events after filtering 0 events from LevelDb fast file: /workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/tw034.SSTABLE
I0000 00:00:1758874323.927447  944026 trace_events.cc:398] Added 7298524 visible events from LevelDb fast file: /workspace/

In [4]:
metadata = TraceEventUtils.get_metadata(data_pb)
tree.build_tree(metadata=metadata, pb_file_name=profile_filepath)

I0000 00:00:1758874394.680479  944026 xplane_to_tools_data.cc:388] serving tool: tool_names with options: {}
Received old tool format: graph_viewer^; mapped to new format: graph_viewer
I0000 00:00:1758874396.607913  944026 xplane_to_tools_data.cc:388] serving tool: graph_viewer with options: {graph_width:2:0;module_name:jit__multi_slice(35):1;node_name::1;show_metadata:1:0;merge_fusion:1:0;type:long_txt:1;}
Received old tool format: graph_viewer^; mapped to new format: graph_viewer
I0000 00:00:1758874396.610556  944026 xplane_to_tools_data.cc:388] serving tool: graph_viewer with options: {graph_width:2:0;show_metadata:1:0;module_name:jit_raw_generate_synthetic_data(33):1;node_name::1;merge_fusion:1:0;type:long_txt:1;}
Received old tool format: graph_viewer^; mapped to new format: graph_viewer
I0000 00:00:1758874396.612590  944026 xplane_to_tools_data.cc:388] serving tool: graph_viewer with options: {graph_width:2:0;show_metadata:1:0;module_name:jit_fold_in(37):1;node_name::1;merge_fusi

Multiple matching hlo_filenames:
['/workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/jit_add(1521).hlo_proto.pb', '/workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/jit_add(1519).hlo_proto.pb', '/workspace/code/traces/logs/20250509_1604_mixtral/tw034/20250509_1604_mixtral/tensorboard/plugins/profile/2025_05_09_16_09_12/jit_add(1515).hlo_proto.pb']


I0000 00:00:1758874398.352022  944026 xplane_to_tools_data.cc:388] serving tool: graph_viewer with options: {graph_width:2:0;show_metadata:1:0;module_name:jit__where(1523):1;node_name::1;merge_fusion:1:0;type:long_txt:1;}


Missing hlo_op:  %copy.5323
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.224.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.225.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.226.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.227.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.228.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.229.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.230.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.231.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.232.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.233.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.234.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.235.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.236.1
in hlo_module:  jit_train_step
Missing hlo_op:  %all-to-all.237.1
in hlo_module:  jit_train_step
Missing hlo_op:  

In [5]:
comm_set = set()
for event in tree.events:
    if event.get("gpu_kernel_op_cat","") == "Communication rccl/nccl":
        comm_set.add(event.get("args","").get("hlo_op","NA"))    

In [6]:
for key in comm_set:
    print(f"Hlo-op : {key}")
    print(tree.hlo_ops["jit_train_step"].get(f"%{key}","Missing"))

Hlo-op : all-gather-start.143
{'output': '((bf16[1,768,48,128]{3,2,0,1},bf16[1,768,8,128]{3,2,0,1},bf16[1,768,8,128]{3,2,0,1})', 'operands': ['bf16[1,6144,48,128]{3,2,0,1}', 'bf16[1,6144,8,128]{3,2,0,1}', 'bf16[1,6144,8,128]{3,2,0,1}'], 'computation': 'rest', 'metadata': 'metadata={scheduling_name="all-gather-start.143"', 'backend_config': 'backend_config={"operation_queue_id":"0","wait_on_operation_queues":[],"collective_backend_config":{"is_sync":false,"no_parallel_custom_call":false,"is_pipelined":false},"force_earliest_schedule":false}', 'replica_groups': 'replica_groups={{0,1,2,3,4,5,6,7},{8,9,10,11,12,13,14,15},{16,17,18,19,20,21,22,23},{24,25,26,27,28,29,30,31}}'}
Hlo-op : all-to-all.244.0.double_buffer_clone.1
Missing
Hlo-op : all-gather-start.10
{'output': '(bf16[16384,8]{1,0},bf16[65536,8]{1,0})', 'operands': ['%bitcast.121271.0'], 'computation': 'rest', 'metadata': 'metadata={scheduling_name="all-gather-start.10"', 'backend_config': 'backend_config={"operation_queue_id":"0",